In [1]:
# Cell 1

import pandas as pd
import geopandas as gpd
import numpy as np
import re
from shapely.geometry import Point
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from folium.plugins import HeatMap
from geopy.geocoders import Nominatim
import time
import requests
import os
from IPython.display import display, IFrame
from geopy.geocoders import ArcGIS
from time import sleep
from datetime import timedelta



In [2]:
# Cell 2

# import dataset to work with
pickup_report = pd.read_csv('trash_hauler_report.csv')


In [3]:
# Cell 3

pickup_report.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20226 entries, 0 to 20225
Data columns (total 11 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Request Number    20226 non-null  int64  
 1   Date Opened       20226 non-null  object 
 2   Request           20226 non-null  object 
 3   Description       20195 non-null  object 
 4   Incident Address  20217 non-null  object 
 5   Zip Code          20151 non-null  float64
 6   Trash Hauler      19325 non-null  object 
 7   Trash Route       19279 non-null  object 
 8   Council District  20177 non-null  float64
 9   State Plan X      20198 non-null  float64
 10  State Plan Y      20198 non-null  float64
dtypes: float64(4), int64(1), object(6)
memory usage: 1.7+ MB


In [4]:
#Cell 4

# Fill missing fields 
pickup_report['Trash Hauler'] = pickup_report['Trash Hauler'].fillna('N/A')
pickup_report['Trash Route'] = pickup_report['Trash Route'].fillna('N/A')


In [5]:
# Cell 5

# code from Logan to handle zip code disparities
pickup_report['Zip Code'] = pickup_report['Zip Code'].fillna(0).astype('category')
assert pickup_report['Zip Code'].dtype == 'category'

print(pickup_report['Zip Code'].describe())

display(pickup_report['Zip Code'])

count     20226.0
unique       29.0
top       37013.0
freq       2278.0
Name: Zip Code, dtype: float64


0        37207.0
1        37218.0
2        37209.0
3        37207.0
4        37209.0
          ...   
20221    37013.0
20222    37206.0
20223    37214.0
20224    37013.0
20225    37217.0
Name: Zip Code, Length: 20226, dtype: category
Categories (29, float64): [0.0, 37013.0, 37027.0, 37076.0, ..., 37219.0, 37220.0, 37221.0, 37228.0]

In [6]:
# Cell 6

# Clean up column names and Normalize data
pickup_report = pickup_report.rename(columns={'Request ': 'Request'})
pickup_report['Trash Hauler'] = pickup_report['Trash Hauler'].str.upper()

In [7]:
# Cell 7

# Create a dataframe made up of ONLY 'missed' appearing in the 'Request" column
missedpu = pickup_report[pickup_report['Request'].str.contains(r'\bmissed\b', case=False, na=False, regex=True)]
print (missedpu.head(25))



    Request Number Date Opened                               Request  \
1            25274    11/01/17  Trash - Curbside/Alley Missed Pickup   
2            25276    11/01/17  Trash - Curbside/Alley Missed Pickup   
3            25307    11/01/17  Trash - Curbside/Alley Missed Pickup   
4            25312    11/01/17  Trash - Curbside/Alley Missed Pickup   
8            25330    11/01/17  Trash - Curbside/Alley Missed Pickup   
9            25331    11/01/17  Trash - Curbside/Alley Missed Pickup   
10           25341    11/01/17  Trash - Curbside/Alley Missed Pickup   
12           25359    11/01/17  Trash - Curbside/Alley Missed Pickup   
14           25370    11/01/17  Trash - Curbside/Alley Missed Pickup   
15           25371    11/01/17  Trash - Curbside/Alley Missed Pickup   
18           25449    11/01/17  Trash - Curbside/Alley Missed Pickup   
19           25454    11/01/17  Trash - Curbside/Alley Missed Pickup   
21           25469    11/01/17  Trash - Curbside/Alley Missed Pi

In [8]:
# Cell 8

# count number of times an address was missed

add_counts = missedpu.groupby(missedpu['Incident Address'].str.lower()).size().reset_index(name='Missed Count')
miss_count = missedpu.merge(add_counts[add_counts['Missed Count'] > 1], left_on=missedpu['Incident Address'].str.lower(), right_on='Incident Address', how='inner')[['Missed Count'] + [col for col in missedpu.columns]].rename(columns={'Incident Address_x': 'Incident Address'})
print(miss_count.head(20))

    Missed Count  Request Number Date Opened  \
0              2           25274    11/01/17   
1              2           25359    11/01/17   
2              4           25371    11/01/17   
3              3           25454    11/01/17   
4              5           25496    11/01/17   
5              2           25511    11/01/17   
6              2           25512    11/01/17   
7              4           25515    11/01/17   
8              3           25517    11/01/17   
9              2           25536    11/02/17   
10             4           25539    11/02/17   
11             2           25540    11/02/17   
12             2           25586    11/02/17   
13             5           25587    11/02/17   
14             5           25592    11/02/17   
15             2           25653    11/02/17   
16             3           25733    11/02/17   
17             5           25789    11/02/17   
18             2           25791    11/02/17   
19             2           25825    11/0

In [9]:
# Cell 9

# add fees

fees = ((miss_count['Missed Count'] -1) * 200)
tot_fees = ((miss_count['Missed Count'] -1).sum())*200

# add column to dataframe
miss_count['fees'] = (miss_count['Missed Count'] - 1) * 200

# total fees
print(tot_fees)

# fees by address in table: 
print(miss_count[['Missed Count', 'fees', 'Incident Address', 'Zip Code']].head(25))




3016400
    Missed Count  fees        Incident Address Zip Code
0              2   200   4028 clarksville pike  37218.0
1              2   200         830 meridian st  37207.0
2              4   600   2218 buena vista pike  37218.0
3              3   400         449 westboro dr  37209.0
4              5   800      1815 woodmont blvd  37215.0
5              2   200         259 sunrise ave  37211.0
6              2   200         4311 dakota ave  37209.0
7              4   600         4029 graybar ct  37215.0
8              3   400          524 harding pl  37211.0
9              2   200  6011 jocelyn hollow rd  37205.0
10             4   600         2524 batavia st  37208.0
11             2   200          934 battery ln  37220.0
12             2   200         4311 dakota ave  37209.0
13             5   800    101 westover park ct  37215.0
14             5   800      205 channelkirk ln  37215.0
15             2   200    118 westover park ct  37215.0
16             3   400       905 woodmon

In [10]:
# Cell 10

# missed counts by route with fees inclusive

route_missed = miss_count.groupby('Trash Route').agg({'Missed Count': 'sum', 'fees': 'sum'})
print(route_missed)

             Missed Count    fees
Trash Route                      
1201                  143   18000
1202                   58    6600
1203                   18    1800
1204                   33    3600
1205                   51    8400
...                   ...     ...
9505                    4     400
9506                   50    5600
9507                   24    2400
9508                  108   13200
N/A                  1303  196600

[162 rows x 2 columns]


In [11]:
# Cell 11

# Trash Route N/A concerning.  Exploring possible reasons

na_explore = miss_count[miss_count['Trash Route'] == 'N/A'][['Request', 'Description', 'Trash Hauler', 'Incident Address']]
print(na_explore.head(50))

# Missed pickups seem valid even though there is no Trash Route recorded.  Might warrent more investigation later

                                   Request  \
34    Trash - Curbside/Alley Missed Pickup   
35    Trash - Curbside/Alley Missed Pickup   
65    Trash - Curbside/Alley Missed Pickup   
66    Trash - Curbside/Alley Missed Pickup   
67    Trash - Curbside/Alley Missed Pickup   
68    Trash - Curbside/Alley Missed Pickup   
173   Trash - Curbside/Alley Missed Pickup   
179   Trash - Curbside/Alley Missed Pickup   
180   Trash - Curbside/Alley Missed Pickup   
181   Trash - Curbside/Alley Missed Pickup   
189   Trash - Curbside/Alley Missed Pickup   
245   Trash - Curbside/Alley Missed Pickup   
261   Trash - Curbside/Alley Missed Pickup   
266   Trash - Curbside/Alley Missed Pickup   
288   Trash - Curbside/Alley Missed Pickup   
297   Trash - Curbside/Alley Missed Pickup   
303   Trash - Curbside/Alley Missed Pickup   
319   Trash - Curbside/Alley Missed Pickup   
329   Trash - Curbside/Alley Missed Pickup   
348   Trash - Curbside/Alley Missed Pickup   
390   Trash - Curbside/Alley Misse

In [12]:
# Cell 12
# Prepare data for heatmap

# Create copy to preserve original
miss_count_copy = miss_count.copy()

# Convert Zip Code to string and truncate to 5 digits
miss_count_copy['Zip Code'] = miss_count_copy['Zip Code'].apply(
    lambda x: str(int(x))[:5] if pd.notna(x) else None
)

# Load Tennessee GeoJSON
geojson_file = 'zipcodes.geojson'
if not os.path.exists(geojson_file):
    print(f"ERROR: File '{geojson_file}' not found in {os.getcwd()}.")
else:
    zip_gdf = gpd.read_file(geojson_file)
    zip_gdf['Zip Code'] = zip_gdf['zip'].astype(str)  # Use 'zip' column

    # Calculate centroids in WGS84 (EPSG:4326) for folium
    zip_gdf['Latitude'] = zip_gdf['geometry'].centroid.y  # Degrees
    zip_gdf['Longitude'] = zip_gdf['geometry'].centroid.x  # Degrees

    # Merge centroids
    miss_count_copy = miss_count_copy.merge(
        zip_gdf[['Zip Code', 'Latitude', 'Longitude']],
        on='Zip Code',
        how='left'
    )

# Group fees by zip code
zip_fees = miss_count_copy.groupby('Zip Code', observed=False).agg({
    'fees': 'sum'
}).reset_index()

C:\Users\miken\AppData\Local\Temp\ipykernel_66804\709594375.py:21: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  zip_gdf['Latitude'] = zip_gdf['geometry'].centroid.y  # Degrees
C:\Users\miken\AppData\Local\Temp\ipykernel_66804\709594375.py:22: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  zip_gdf['Longitude'] = zip_gdf['geometry'].centroid.x  # Degrees


In [13]:
# Cell 13
# Heatmap using zip code centroids

# Remove rows with missing coordinates
miss_count_copy = miss_count_copy.dropna(subset=['Latitude', 'Longitude'])

# Merge boundaries
zip_boundaries = zip_gdf[['Zip Code', 'geometry']].merge(zip_fees, on='Zip Code', how='inner')

# Create heatmap data
heat_data = [[row['Latitude'], row['Longitude'], row['fees'] / 200] for _, row in miss_count_copy.iterrows()]
heat_data.append([36.1627, -86.7819, 1])  # Nashville test point

# Create map
center_lat = miss_count_copy['Latitude'].mean()
center_lon = miss_count_copy['Longitude'].mean()
if pd.isna(center_lat) or pd.isna(center_lon) or not (35 < center_lat < 37 and -88 < center_lon < -86):
    center_lat, center_lon = 36.1627, -86.7819  # Nashville fallback
m = folium.Map(location=[center_lat, center_lon], zoom_start=10, tiles='CartoDB Positron')


# Add heatmap
HeatMap(heat_data, radius=25, blur=10, min_opacity=0.5, max_zoom=13, name='Fees Heatmap').add_to(m)

# Add semi-transparent boundaries
folium.GeoJson(
    zip_boundaries,
    style_function=lambda feature: {
        'color': 'blue',
        'weight': 2,
        'opacity': 0.5,
        'fillOpacity': 0
    },
    tooltip=folium.GeoJsonTooltip(fields=['Zip Code', 'fees'], aliases=['Zip Code', 'Fees'])
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save and display
m.save('fees_heatmap_by_address.html')
print("Map saved as 'fees_heatmap_by_address.html'.")
display(m)

Map saved as 'fees_heatmap_by_address.html'.


In [14]:
zip_gdf = gpd.read_file('zipcodes.geojson')
print("Fees summary:", miss_count_copy['fees'].describe())

Fees summary: count    6702.000000
mean      493.822739
std       512.392940
min       200.000000
25%       200.000000
50%       200.000000
75%       600.000000
max      3600.000000
Name: fees, dtype: float64


In [15]:
# Cell 14
# Heatmap using actual addresses from miss_count

# Cache file for geocoded addresses
cache_file = 'geocoded_addresses.csv'

# Function to geocode
def geocode_address(address):
    address = address.strip().title() + ", Nashville, TN, USA"
    location = geolocator.geocode(address)
    return (location.latitude, location.longitude) if location else (None, None)

# Load or create geocoded cache
if os.path.exists(cache_file):
    geocoded_cache = pd.read_csv(cache_file)
else:
    geocoded_cache = pd.DataFrame(columns=['Incident Address', 'Latitude', 'Longitude'])

# Copy miss_count
address_df = miss_count[['Incident Address', 'fees']].copy()

# Merge with cached geocoded data
address_df = address_df.merge(geocoded_cache, on='Incident Address', how='left')

# Save cache
geocoded_cache.to_csv(cache_file, index=False)

# Merge geocoded coordinates back
address_df = address_df.drop(['Latitude', 'Longitude'], axis=1, errors='ignore')
address_df = address_df.merge(geocoded_cache, on='Incident Address', how='left')

# Remove rows with missing coordinates
address_df = address_df.dropna(subset=['Latitude', 'Longitude'])

# Create heatmap data
heat_data = [[row['Latitude'], row['Longitude'], row['fees'] / 200] for _, row in address_df.iterrows()]

# Create map
center_lat = address_df['Latitude'].mean()
center_lon = address_df['Longitude'].mean()
if pd.isna(center_lat) or pd.isna(center_lon) or not (35 < center_lat < 37 and -88 < center_lon < -86):
    center_lat, center_lon = 36.1627, -86.7819  # Nashville fallback
m = folium.Map(location=[center_lat, center_lon], zoom_start=10, tiles='CartoDB Positron')

# Add heatmap
HeatMap(heat_data, radius=15, blur=10, min_opacity=0.5, max_zoom=13, name='Fees Heatmap').add_to(m)

# Add semi-transparent boundaries
folium.GeoJson(
    zip_boundaries,
    style_function=lambda feature: {
        'color': 'blue',
        'weight': 2,
        'opacity': 0.5,
        'fillOpacity': 0
    },
    tooltip=folium.GeoJsonTooltip(fields=['Zip Code', 'fees'], aliases=['Zip Code', 'Fees'])
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save and display
m.save('fees_heatmap_by_actual_address.html')
display(m)

In [16]:
# Cell 15

# Create a dataframe made up of ONLY 'notmissed' appearing in the 'Request" column
notmissedpu = pickup_report[~pickup_report['Request'].str.contains(r'\bmissed\b', case=False, na=False, regex=True)]
print(notmissedpu.head(10))



    Request Number Date Opened                     Request  \
0            25270    11/01/17            Trash - Backdoor   
5            25317    11/01/17  Trash Collection Complaint   
6            25325    11/01/17          Damage to Property   
7            25327    11/01/17  Trash Collection Complaint   
11           25350    11/01/17  Trash Collection Complaint   
13           25366    11/01/17  Trash Collection Complaint   
16           25393    11/01/17  Trash Collection Complaint   
17           25407    11/01/17  Trash Collection Complaint   
20           25465    11/01/17  Trash Collection Complaint   
27           25508    11/01/17  Trash Collection Complaint   

                                          Description        Incident Address  \
0   house with the wheel chair ramp, they share dr...          3817 Crouch Dr   
5   left trash cart in middle of driveway instead ...          3602 floral dr   
6   Trash/emptied Wednesday & now metal black-mail...        4721 Chalmers

In [17]:
# Cell 16
# Display unique 'Request' values and their counts in descending order
request_counts = notmissedpu['Request'].value_counts().reset_index()
request_counts.columns = ['Request', 'Count']
print(request_counts)

                      Request  Count
0            Trash - Backdoor   2629
1  Trash Collection Complaint   2312
2          Damage to Property    257


In [18]:
# Cell 17

# How does METRO crew compare to the contractors
# Count number of requests per Trash Hauler
hauler_report = pickup_report.groupby('Trash Hauler')['Request'].count().reset_index(name='Request Count')
hauler_report = hauler_report.sort_values(by='Request Count', ascending=False)
print(hauler_report)

  Trash Hauler  Request Count
2    RED RIVER          14395
0        METRO           3580
3    WASTE IND           1350
1          N/A            901


In [19]:
# Cell 18

# Fees and Missed Count by Trash Hauler
hauler_fees = miss_count.groupby('Trash Hauler')[['fees', 'Missed Count']].sum().reset_index()
hauler_fees = hauler_fees.sort_values(by='fees', ascending=False)
print(hauler_fees)

  Trash Hauler     fees  Missed Count
2    RED RIVER  2181200         15245
0        METRO   484800          3507
1          N/A   179000          1201
3    WASTE IND   171400          1253


In [20]:
# Cell 19

# Fees and Missed Count by Trash Hauler
route_fees = miss_count.groupby('Trash Route')[['fees', 'Missed Count']].sum().reset_index()
route_fees = route_fees.sort_values(by='fees', ascending=False)
print(route_fees)

    Trash Route    fees  Missed Count
161         N/A  196600          1303
123        4504  114800           736
35         2303  107200           608
129        4510   92800           540
137        9208   85800           530
..          ...     ...           ...
69        3303S     400             4
104        4301     400             4
103        4210     400             4
135        9206     400             4
157        9505     400             4

[162 rows x 3 columns]


In [21]:
# Cell 19

# Export pickup_report to CSV for Tableau
pickup_report.to_csv('pickup_report.csv', index=False)
# add column to dataframe
miss_count.to_csv('miss_count.csv')

In [22]:
drop_cols = [col for col in miss_count.columns if col.endswith('_y')]
miss_count = miss_count.drop(columns=drop_cols)
rename_cols = {col: col.replace('_x', '') for col in miss_count.columns if col.endswith('_x')}
miss_count = miss_count.rename(columns=rename_cols)
print(miss_count.columns.tolist())

['Missed Count', 'Request Number', 'Date Opened', 'Request', 'Description', 'Incident Address', 'Zip Code', 'Trash Hauler', 'Trash Route', 'Council District', 'State Plan X', 'State Plan Y', 'fees']


In [23]:
# Cell 20

# Add Alt_A_Fees to miss_count: $1500 per 3+ missed pickups within 180 days, else 0
miss_count['Date Opened'] = pd.to_datetime(miss_count['Date Opened'])

# Function to count sets of 3+ missed pickups within 180 days
def calc_alt_fees(dates):
    dates = sorted(dates.dropna().unique())
    if len(dates) < 3:
        return 0
    count = 0
    for i in range(len(dates) - 2):
        window_end = dates[i] + pd.Timedelta(days=180)
        window_dates = [d for d in dates[i:] if d <= window_end]
        if len(window_dates) >= 3:
            count += 1
            i += len(window_dates) - 1
    return count * 1500

# Calculate Alt_A_Fees by Incident Address
alt_a_fees = miss_count.groupby('Incident Address')['Date Opened'].apply(calc_alt_fees).reset_index()
alt_a_fees.columns = ['Incident Address', 'Alt_A_Fees']

# Merge Alt_A_Fees into miss_count
miss_count = miss_count.merge(alt_a_fees, on='Incident Address', how='left')
miss_count['Alt_A_Fees'] = miss_count['Alt_A_Fees'].fillna(0).astype(int)

print("Added Alt_A_Fees to miss_count")
print(miss_count[['Incident Address', 'Missed Count', 'fees', 'Alt_A_Fees']].head(25))

Added Alt_A_Fees to miss_count
          Incident Address  Missed Count  fees  Alt_A_Fees
0    4028 clarksville pike             2   200           0
1          830 meridian st             2   200           0
2    2218 buena vista pike             4   600           0
3          449 westboro dr             3   400           0
4       1815 woodmont blvd             5   800           0
5          259 sunrise ave             2   200           0
6          4311 dakota ave             2   200           0
7          4029 graybar ct             4   600           0
8           524 harding pl             3   400           0
9   6011 jocelyn hollow rd             2   200           0
10         2524 batavia st             4   600        1500
11          934 battery ln             2   200           0
12         4311 dakota ave             2   200           0
13    101 westover park ct             5   800        3000
14      205 channelkirk ln             5   800           0
15    118 westover park c

C:\Users\miken\AppData\Local\Temp\ipykernel_66804\1677550948.py:4: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  miss_count['Date Opened'] = pd.to_datetime(miss_count['Date Opened'])


In [24]:
print(f"Total fees: {miss_count['fees'].sum()}, Total Alt_A_Fees: {miss_count['Alt_A_Fees'].sum()}")

Total fees: 3016400, Total Alt_A_Fees: 10324500


In [25]:
miss_count.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6124 entries, 0 to 6123
Data columns (total 14 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   Missed Count      6124 non-null   int64         
 1   Request Number    6124 non-null   int64         
 2   Date Opened       6124 non-null   datetime64[ns]
 3   Request           6124 non-null   object        
 4   Description       6116 non-null   object        
 5   Incident Address  6124 non-null   object        
 6   Zip Code          6124 non-null   category      
 7   Trash Hauler      6124 non-null   object        
 8   Trash Route       6124 non-null   object        
 9   Council District  6117 non-null   float64       
 10  State Plan X      6118 non-null   float64       
 11  State Plan Y      6118 non-null   float64       
 12  fees              6124 non-null   int64         
 13  Alt_A_Fees        6124 non-null   int64         
dtypes: category(1), datetime

In [26]:
# Cell 24
import geopandas as gpd
# Create a copy to avoid modifying a slice
missedpu_copy = missedpu.copy()
gdf = gpd.GeoDataFrame(missedpu_copy, geometry=gpd.points_from_xy(missedpu_copy['State Plan X'], missedpu_copy['State Plan Y']), crs='EPSG:2276')
gdf = gdf.to_crs(epsg=4326)
missedpu_copy.loc[:, 'Longitude'] = gdf.geometry.x
missedpu_copy.loc[:, 'Latitude'] = gdf.geometry.y
missedpu_copy.to_csv('missedpu_wgs84.csv', index=False)
print("Exported to missedpu_wgs84.csv")

Exported to missedpu_wgs84.csv
